In [23]:
import pandas as pd
import numpy as np
import geopandas as gpd
from shapely.geometry import Point, Polygon

from scipy.spatial import cKDTree
import haversine as hs  # pip install haversine



# Nearest distance with haversine function

In [53]:
# import hospital data as geodataframe
gdf_spital = gpd.read_file(r'C:\Users\gigim\Documents\GitHub\mlp\geodata\\data_spital.gpkg')
gdf_laerm = gpd.read_file(r'C:\Users\gigim\Documents\GitHub\mlp\geodata\\data_strassenlaerm.gpkg')
gdf_ov = gpd.read_file(r'C:\Users\gigim\Documents\GitHub\mlp\geodata\\Haltestellen_des_offentlichen_Verkehrs_-OGD.gpkg')





In [ ]:
# read csv file of addresses with long and lat
df_24 = pd.read_csv('immoscout24_geocoded.csv', delimiter='|')

In [12]:
gdf_ov = gpd.read_file(r'C:\Users\gigim\Documents\GitHub\mlp\geodata\\Haltestellen_des_offentlichen_Verkehrs_-OGD.gpkg')

In [7]:

# remove nan values in geodaraframe
print(df_24.shape)
# Filter out rows where 'geometry' is NaN
df_24.dropna(subset=['longitude'], inplace=True)
print(df_24.shape)



(641, 31)
(637, 31)


In [13]:
#convert geoDataFrame to DF
def todf(gdf):
    # Transform to WGS 84 CRS
    gdf = gdf.to_crs(epsg=4326)
    # First ensure that your geometries are points
    assert all(gdf.geometry.geom_type == 'Point'), "All geometries must be Points."

    # Create longitude and latitude columns from the geometry
    gdf['longitude'] = gdf.geometry.x
    gdf['latitude'] = gdf.geometry.y

    # Now convert your GeoDataFrame to a DataFrame
    df = pd.DataFrame(gdf.drop(columns='geometry'))

df_spital = todf(gdf_spital)
df_laerm = todf(gdf_laerm)
df_ov = todf(gdf_ov)


In [38]:
# Calculate distance using haversine (Quelle: https://towardsdatascience.com/calculating-distance-between-two-geolocations-in-python-26ad3afe287b, https://pypi.org/project/haversine/)
# pöd version with kdtree runns faster
def distance(df_add, df_24):

    for index, row in df_24.iterrows():
        loc1 = (row['latitude'], row['longitude'])
        print(loc1)
        min_distance = float('inf')
        for index2, row2 in df_add.iterrows():
            loc2 = (row2['latitude'], row2['longitude'])
            print(loc2)
            distance = hs.haversine(loc1,loc2)
            if distance < min_distance:
                df_24.at[index, 'distance_hosp'] = distance
                min_distance = distance
    return df_24

    

In [48]:
# with kd tree by chat gpt

def calculate_distance2(df_add, df_24, distance_type: str, laerm=False):
    # Convert DataFrame columns to numpy arrays for KD-Tree
    tree = cKDTree(df_add[['latitude', 'longitude']].to_numpy())
    distances, indices = tree.query(df_24[['latitude', 'longitude']].to_numpy(), k=1)

    # Convert distances from degrees (output by KD-Tree) to kilometers using haversine
    df_24[distance_type] = [hs.haversine(df_24[['latitude', 'longitude']].iloc[i], df_add[['latitude', 'longitude']].iloc[indices[i]]) for i in range(len(indices))]
    
    return df_24


def calculate_distance(df_add, df_24, distance_type: str, laerm=False):
    # Ensure the dataframes have the correct index type
    df_add = df_add.reset_index(drop=True)
    df_24 = df_24.reset_index(drop=True)
    
    # Convert DataFrame columns to numpy arrays for KD-Tree
    tree = cKDTree(df_add[['latitude', 'longitude']].to_numpy())
    distances, indices = tree.query(df_24[['latitude', 'longitude']].to_numpy(), k=1)

    # Pre-compute the locations as a list of tuples for efficiency
    df_24_locs = list(df_24[['latitude', 'longitude']].itertuples(index=False, name=None))
    df_add_locs = list(df_add[['latitude', 'longitude']].itertuples(index=False, name=None))

    # Calculate haversine distances and store in the specified column
    df_24[distance_type] = [hs.haversine(df_24_locs[i], df_add_locs[indices[i]]) for i in range(len(indices))]
    
    # If laerm is True, transfer 'lr_day' and 'lr_night' from df_add to df_24
    if laerm:
        df_24['lr_day'] = [df_add.loc[indices[i], 'lr_day'] for i in range(len(indices))]
        df_24['lr_night'] = [df_add.loc[indices[i], 'lr_night'] for i in range(len(indices))]

    return df_24

In [52]:
from scipy.spatial import cKDTree
import haversine as hs
import pandas as pd

def calculate_distance(df_add, df_24, distance_type: str, laerm=False):
    # Ensure the dataframes have the correct index type
    df_add = df_add.reset_index(drop=True)
    df_24 = df_24.reset_index(drop=True)
    
    # Convert DataFrame columns to numpy arrays for KD-Tree
    tree = cKDTree(df_add[['latitude', 'longitude']].to_numpy())
    distances, indices = tree.query(df_24[['latitude', 'longitude']].to_numpy(), k=1)

    # Pre-compute the locations as a list of tuples for efficiency
    df_24_locs = list(df_24[['latitude', 'longitude']].itertuples(index=False, name=None))
    df_add_locs = list(df_add[['latitude', 'longitude']].itertuples(index=False, name=None))

    # If laerm is False, calculate and store the haversine distances
    if not laerm:
        df_24[distance_type] = [hs.haversine(df_24_locs[i], df_add_locs[indices[i]]) for i in range(len(indices))]
    else:
        # If laerm is True, transfer 'lr_day' and 'lr_night' from df_add to df_24
        df_24['lr_day'] = [df_add.iloc[indices[i]]['lr_day'] for i in range(len(indices))]
        df_24['lr_night'] = [df_add.iloc[indices[i]]['lr_night'] for i in range(len(indices))]
    
    return df_24

In [49]:
df_24 = calculate_distance(df_spital, df_24, 'distance_hospital')
df_24 = calculate_distance(df_laerm, df_24, 'distance_laerm', True)
df_24 = calculate_distance(df_ov, df_24, 'distance_ov')




In [51]:
df_24.to_clipboard()

In [39]:
df_24_spit_2 = distance(df_spital, df_24)

(47.36455535888672, 8.597229957580566)
(47.366046535465344, 8.497454843595955)
(47.39887122032686, 8.520575505422714)
(47.39887122032686, 8.520575505422714)
(47.39887122032686, 8.520575505422714)
(47.39887122032686, 8.520575505422714)
(47.39887122032686, 8.520575505422714)
(47.39887122032686, 8.520575505422714)
(47.39887122032686, 8.520575505422714)
(47.39887122032686, 8.520575505422714)
(47.366046535465344, 8.497454843595955)
(47.366046535465344, 8.497454843595955)
(47.398306252194175, 8.520391811987091)
(47.366046535465344, 8.497454843595955)
(47.366046535465344, 8.497454843595955)
(47.39870512330968, 8.521022558387239)
(47.39887122032686, 8.520575505422714)
(47.366046535465344, 8.497454843595955)
(47.366046535465344, 8.497454843595955)
(47.366046535465344, 8.497454843595955)
(47.39887122032686, 8.520575505422714)
(47.39887122032686, 8.520575505422714)
(47.366046535465344, 8.497454843595955)
(47.366046535465344, 8.497454843595955)
(47.366046535465344, 8.497454843595955)
(47.366046535

In [46]:
df_laerm_dist =calculate_distance3(df_laerm, df_24, 'distance_laerm', True)

In [47]:
df_laerm_dist

page                             type  price  \
0       2  4.5 Zimmer, 107m², CHF 3’082.–    3082   
1       2   3.5 Zimmer, 77m², CHF 2’443.–    2443   
2       2  4.5 Zimmer, 150m², CHF 5’850.–    5850   
3       2         5.5 Zimmer, CHF 5’500.–    5500   
4       2     3 Zimmer, 81m², CHF 2’610.–    2610   
..    ...                              ...    ...   
632    43   1.5 Zimmer, 34m², CHF 2’120.–    2120   
633    43     2 Zimmer, 50m², CHF 2’430.–    2430   
634    43     2 Zimmer, 49m², CHF 2’320.–    2320   
635    43         3.5 Zimmer, CHF 2’570.–    2570   
636    43                       CHF 180.–     180   

                            address_x  \
0       In der Looren 56, 8053 Zürich   
1    Kügeliloostrasse 99, 8046 Zürich   
2          Wirzenweid 27, 8053 Zürich   
3               Lyrenweg, 8047 Zürich   
4           Röslistr. 57, 8006 Zürich   
..                                ...   
632       Moosstrasse 39, 8038 Zürich   
633       Moosstrasse 39, 8038 Zürich   
634       Moosstrasse 39, 8038 Zürich   
635        Sperletweg 36, 8052 Zürich   
636      Feldblumenweg 5, 8048 Zürich   

                                           description  \
0                               Ihre neue Wohlfühloase   
1               Moderne Wohnung mit gemütlicher Loggia   
2    Bright apartment with the view in a quiet neig...   
3         Haus: In der Stadt Zürich und doch idyllisch   
4       zentral gelegene Wohnung - Mieten ohne Kaution   
..                                                 ...   
632  Erstbezug einer einmaligen Attika-Wohnung in Z...   
633                   Erstbezug in Zürich Wollishofen!   
634                   Erstbezug in Zürich Wollishofen!   
635             3.5 Zimmerwohnung im Eigentumsstandart   
636      Lagerraum in kleinem MFH in Zürich-Altstetten   

                                               weblink       rooms   size  \
0    https://www.immoscout24.ch/de/immobilien/miete...  4.5 Zimmer  107m²   
1    https://www.immoscout24.ch/de/immobilien/miete...  3.5 Zimmer   77m²   
2    https://www.immoscout24.ch/de/immobilien/miete...  4.5 Zimmer  150m²   
3    https://www.immoscout24.ch/de/immobilien/miete...  5.5 Zimmer    NaN   
4    https://www.immoscout24.ch/de/immobilien/miete...    3 Zimmer   81m²   
..                                                 ...         ...    ...   
632  https://www.immoscout24.ch/de/immobilien/miete...  1.5 Zimmer   34m²   
633  https://www.immoscout24.ch/de/immobilien/miete...    2 Zimmer   50m²   
634  https://www.immoscout24.ch/de/immobilien/miete...    2 Zimmer   49m²   
635  https://www.immoscout24.ch/de/immobilien/miete...  3.5 Zimmer    NaN   
636  https://www.immoscout24.ch/de/immobilien/miete...         NaN    NaN   

           price2  1 zimmer  ...  size_num                         address_y  \
0    CHF 3’082.–          0  ...     107.0     In der Looren 56, 8053 Zürich   
1    CHF 2’443.–          0  ...      77.0  Kügeliloostrasse 99, 8046 Zürich   
2    CHF 5’850.–          0  ...     150.0        Wirzenweid 27, 8053 Zürich   
3    CHF 5’500.–          0  ...       NaN             Lyrenweg, 8047 Zürich   
4    CHF 2’610.–          0  ...      81.0             Lyrenweg, 8047 Zürich   
..            ...       ...  ...       ...                               ...   
632  CHF 2’120.–          0  ...      34.0     Forchstrasse 261, 8032 Zürich   
633  CHF 2’430.–          0  ...      50.0     Forchstrasse 261, 8032 Zürich   
634  CHF 2’320.–          0  ...      49.0     Forchstrasse 261, 8032 Zürich   
635  CHF 2’570.–          0  ...       NaN     Forchstrasse 261, 8032 Zürich   
636    CHF 180.–          0  ...       NaN     Forchstrasse 261, 8032 Zürich   

      latitude  longitude                                             detail  \
0    47.364555   8.597230    in der looren 56 8053 zuerich 261 zuerich ch zh   
1    47.415546   8.530204  kuegeliloostrasse 99 8046 zuerich 261 zuerich ...   
2    47.357121   8.583215       wirzenweid 27 8053 z

In [18]:
import pandas as pd
import geopandas as gpd

# Function to convert a GeoDataFrame to a DataFrame and transform CRS
def todf(gdf):
    # Transform to WGS 84 CRS
    gdf = gdf.to_crs(epsg=4326)

    # First ensure that your geometries are points
    assert all(gdf.geometry.geom_type == 'Point'), "All geometries must be Points."

    # Create longitude and latitude columns from the geometry
    gdf['longitude'] = gdf.geometry.x
    gdf['latitude'] = gdf.geometry.y

    # Now convert your GeoDataFrame to a DataFrame by dropping the 'geometry' column
    df = pd.DataFrame(gdf.drop(columns='geometry'))
    return df  # Ensure to return the DataFrame

# Applying the function to the whole GeoDataFrame
df_spital = todf(gdf_spital)
df_laerm = todf(gdf_laerm)
df_ov = todf(gdf_ov)

In [32]:
df_laerm

lr_day  lr_night exposure_limit_value_d exposure_limit_value_n  \
0          26.2      15.9                    <PW                    <PW   
1          27.6      17.3                    <PW                    <PW   
2          28.4      18.3                    <PW                    <PW   
3          29.6      19.5                    <PW                    <PW   
4          25.9      15.7                    <PW                    <PW   
...         ...       ...                    ...                    ...   
2724089    38.3      29.0                    <PW                    <PW   
2724090    34.5      25.3                    <PW                    <PW   
2724091    38.4      29.1                    <PW                    <PW   
2724092    44.8      34.4                    <PW                    <PW   
2724093    37.0      26.9                    <PW                    <PW   

         rel_height_pod  geometry_pod   es        pod_typ operation_status  \
0                  1.72        598.77  2.0  Fassadenpunkt              N/A   
1                  4.62        601.68  2.0  Fassadenpunkt              N/A   
2                  7.53        604.59  2.0  Fassadenpunkt              N/A   
3                 10.44        607.49  2.0  Fassadenpunkt              N/A   
4                  1.72        598.77  2.0  Fassadenpunkt              N/A   
...                 ...           ...  ...            ...              ...   
2724089           57.28        514.90  2.0  Fassadenpunkt              N/A   
2724090           54.58        512.20  2.0  Fassadenpunkt              N/A   
2724091           57.28        514.90  2.0  Fassadenpunkt              N/A   
2724092            8.69        468.34  2.0  Fassadenpunkt              N/A   
2724093            8.69        468.34  2.0  Fassadenpunkt              N/A   

                                      determination_remark  ...       egid  \
0        Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...     157624   
1        Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...     157624   
2        Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...     157624   
3        Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...     157624   
4        Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...     157624   
...                                                    ...  ...        ...   
2724089  Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...  302030867   
2724090  Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...  302030867   
2724091  Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...  302030867   
2724092  Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...     146960   
2724093  Szenario T30 und LAB, Grundlage sonROAD 18 Emi...  ...     146960   

        edid       id_pod  exposure_limit_date           e           n  \
0        N/A  26103468240           2021-12-31  2686958.45  1246277.84   
1        N/A  26103468241           2021-12-31  2686958.45  1246277.84   
2        N/A  26103468242           2021-12-31  2686958.45  1246277.84   
3        N/A  26103468243           2021-12-31  2686958.45  1246277.84   
4        N/A  26103468244           2021-12-31  2686959.08  1246274.99   
...      ...          ...                  ...         ...         ...   
2724089  N/A  26100276351           2021-12-31  2679993.58  1246706.71   
2724090  N/A  26100276352           2021-12-31  2679994.87  1246703.04   
2724091  N/A  26100276353           2021-12-31  2679994.87  1246703.04   
2724092  N/A  26100277252           2021-12-31  2679970.39  1246678.57   
2724093  N/A  26100277253           2021-12-31  2679972.84  1246677.78   

                              lbk_id   objectid  longitude   latitude  
0        SzenT30-LAB_STZH_2020-12-31   112423.0   8.589765  47.361609  
1        SzenT30-LAB_STZH_2020-12-31   112424.0   8.589765  47.361609  
2        SzenT30-LAB_STZH_2020-12-31   112425.0   8.589765  47.361609  
3        SzenT30-LAB_STZH_2020-12-31   112426.0   8.58976